In [1]:
import re
from datetime import datetime as dt

import os
import numpy as np
import pandas as pd
import geopandas as gpd
from shapely.geometry import Point

from cartoframes.auth import set_default_credentials
from cartoframes.viz import Map, Layer, animation_widget, animation_style, basemaps

set_default_credentials('cartoframes')

In [2]:
def get_file_regex(prefix, file_datetime = None, suffix = None, ext = "csv"):
    if file_datetime is None:
        year_re = r"\d{4}"
        month_re = r"[a-zA-Z]{3}"
        day_re = r"\d{2}"
        hr_re = r"\d{2}"
        min_re = r"\d{2}"
        sec_re = r"\d{2}"
    else:
        date_string = file_datetime.strftime("%Y.%b.%d.%H.%M.%S")
        year_re, month_re, day_re, hr_re, min_re, sec_re = date_string.split(".")

    if suffix is None:
        suffix_re = r""
    else:
        suffix_re = r"\." + suffix

    file_re = re.compile(prefix+   r"\.("+ year_re + 
                                        r")\.(" + month_re + 
                                        r")\.(" + day_re    + 
                                        r")\.(" + hr_re +
                                        r")_(" + min_re + 
                                        r")_(" + sec_re + 
                                        r")" +suffix_re + 
                                        r"\." + ext + 
                                        r"")
    return file_re

def most_recent_directory_file(directory, file_regex):
    files = os.listdir(directory)
    filtered_files = [f for f in files if file_regex.search(f) is not None]
    filtered_files.sort(key = lambda x: dt_from_file_name(x, file_regex), reverse=True)
    return filtered_files[0]

def dt_from_file_name(file_name, regex):
    s = regex.search(file_name)
    file_dt = dt.strptime(''.join(s.groups()), "%Y%b%d%H%M%S")
    return file_dt

In [3]:
data_dir = "..\\output\\batch\\model_run_data\\"

project_crs = {'init': 'epsg:27700'}
wsg_crs = {'init':'epsg:4326'}

file_re = get_file_regex("pedestrian_locations")
ped_locations_file = most_recent_directory_file(data_dir, file_re)

df_ped_loc = pd.read_csv(os.path.join(data_dir, ped_locations_file))

# Now split df into one for locations, one for route coords
lo_cols = [i for i in df_ped_loc.columns if 'Loc' in i]

df_loc = df_ped_loc.dropna(subset = lo_cols)
for c in lo_cols:
    df_loc[c] = df_loc[c].map(float)


gdf_loc = gpd.GeoDataFrame(df_loc, geometry=gpd.points_from_xy(df_loc.LocXString, df_loc.LocYString))
gdf_loc.crs = project_crs

gdf_loc = gdf_loc.to_crs(wsg_crs)

C:\Users\obisargoni\.conda\envs\gforge\lib\site-packages\pyproj\crs\crs.py:53: FutureWarning: '+init=<authority>:<code>' syntax is deprecated. '<authority>:<code>' is the preferred initialization method. When making the change, be mindful of axis order changes: https://pyproj4.github.io/pyproj/stable/gotchas.html#axis-order-changes-in-proj-6
  return _prepare_from_string(" ".join(pjargs))


In [4]:
# Creat map for single trajectory
path_1_1 = gdf_loc.loc[(gdf_loc['run'] == 1) & (gdf_loc['ID']==1)]

Map(
        Layer(path_1_1),
        basemap=basemaps.voyager
)

In [5]:
path_1_1.crs

<Geographic 2D CRS: +init=epsg:4326 +type=crs>
Name: WGS 84
Axis Info [ellipsoidal]:
- lon[east]: Longitude (degree)
- lat[north]: Latitude (degree)
Area of Use:
- name: World
- bounds: (-180.0, -90.0, 180.0, 90.0)
Datum: World Geodetic System 1984
- Ellipsoid: WGS 84
- Prime Meridian: Greenwich

In [6]:
# Create animated map with the pedestrian locations

In [7]:
# Filter the data
gdf_run = gdf_loc[(gdf_loc['run']==2)]
n_ticks = max(gdf_run['tick'])

In [161]:
from cartoframes.viz import Source

# Create new data source
pedestrian_paths = Source(gdf_run, credentials=None, geom_col='geometry', encode_data=False)

Map(
Layer(pedestrian_paths, 
      animation_style(
              'tick',
              duration=n_ticks/20,
              fade_in=0, 
              fade_out=0.5, 
              color=None,
              size=5, 
              opacity=None, 
              stroke_color=None, 
              stroke_width=None), 
      widgets=[
        animation_widget(
            title='Simulated Pedestrian Paths',
            description= 'Play, pause, or select the behavioural scenario'
        )],
      encode_data=False),
basemap=basemaps.voyager
)



In [163]:
gdf_run.head()

ID     LocXString     LocYString  tick  run                   geometry
49805   1  530511.504655  180908.692823   1.0    2  POINT (-0.12065 51.51204)
49806   2  530411.266157  180826.821227   1.0    2  POINT (-0.12213 51.51133)
49807   3  530418.086064  180819.928561   1.0    2  POINT (-0.12203 51.51126)
49808   1  530511.820909  180908.418532   2.0    2  POINT (-0.12065 51.51204)
49809   2  530411.546567  180827.067968   2.0    2  POINT (-0.12212 51.51133)

In [55]:
max(pedestrian_paths['tick'])

TypeError: 'Source' object is not subscriptable

In [60]:
n_ticks

330.0